In [60]:
import os

import pandas as pd
import numpy as np

import seaborn as sns
import plotly.graph_objects as go

import statsmodels.tsa.seasonal as smt
import statsmodels.api as sm

from sklearn.preprocessing import MinMaxScaler

from plotly.subplots import make_subplots

from prophet import Prophet

from sklearn.metrics import (
    mean_absolute_error,
    median_absolute_error,
    mean_absolute_percentage_error,
    mean_squared_error,
)

from scipy.stats import pearsonr

In [61]:
data_folder = os.path.join("..", "..", "data", "berlin")

clean_data_folder = os.path.join(data_folder, "clean_data")
projections_folder = os.path.join(data_folder, "projections")

my_projections_folder = os.path.join(projections_folder, "found_by_me")

# Load Clean Data

In [62]:
surface_df = pd.read_excel(
    os.path.join(clean_data_folder, "surface.xlsx")
)
ground_df = pd.read_excel(
    os.path.join(clean_data_folder, "ground.xlsx")
)

flow_river_projections = pd.read_excel(
    os.path.join(my_projections_folder, "flow_river.xlsx")
)

air_temp_projections = pd.read_excel(
    os.path.join(my_projections_folder, "air_temp.xlsx")
)

precip_projections = pd.read_excel(
    os.path.join(my_projections_folder, "precip.xlsx")
)

In [63]:
surface_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1521 entries, 0 to 1520
Data columns (total 17 columns):
 #   Column                         Non-Null Count  Dtype         
---  ------                         --------------  -----         
 0   DateTime                       1521 non-null   datetime64[ns]
 1   Air Temperature (°C)           1521 non-null   float64       
 2   Ammonium (mg/l)                1521 non-null   float64       
 3   BOD (mg/l)                     875 non-null    float64       
 4   Coliform Bacteria (MPN/100ml)  1521 non-null   float64       
 5   Conductivity (µS/cm)           1521 non-null   float64       
 6   DOC (mg/l)                     1521 non-null   float64       
 7   Dissolved Oxygen (mg/l)        1521 non-null   float64       
 8   E.Coli (MPN/100ml)             1521 non-null   float64       
 9   Enterococcus (MPN/100ml)       754 non-null    float64       
 10  Nitrate (mg/l)                 1521 non-null   float64       
 11  TOC (mg/l)       

In [64]:
ground_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 594 entries, 0 to 593
Data columns (total 10 columns):
 #   Column                   Non-Null Count  Dtype         
---  ------                   --------------  -----         
 0   DateTime                 594 non-null    datetime64[ns]
 1   Air Temperature (°C)     594 non-null    float64       
 2   Ammonium (mg/l)          594 non-null    float64       
 3   Conductivity (µS/cm)     594 non-null    float64       
 4   Nitrate (mg/l)           258 non-null    float64       
 5   UVA254 (1/m)             594 non-null    float64       
 6   Water Temperature (°C)   594 non-null    float64       
 7   pH                       594 non-null    float64       
 8   Station                  594 non-null    int64         
 9   Cumulated Rainfall (mm)  594 non-null    float64       
dtypes: datetime64[ns](1), float64(8), int64(1)
memory usage: 46.5 KB


# Bacteria Inspection

In [ ]:
bacteria_info_df = pd.DataFrame(
    index=pd.Index(["Min Value", "Max Value"], name="Info"),
    columns=pd.MultiIndex.from_product(
        [list(stations_dict.keys()), bacteria_columns],
        names=["Station ID", "Parameter"],
    ),
)

In [ ]:
### Bacteria Inspection

fig = go.Figure()

for column in bacteria_columns:
    # Compute % of 0s, min and max for every year.
    min_values = np.array([])
    max_values = np.array([])

    for year in station_df.index.year.unique():
        year_df = station_df[station_df.index.year == year]

        min_value = year_df[column].min()
        max_value = year_df[column].max()

        min_values = np.append(min_values, min_value)
        max_values = np.append(max_values, max_value)

        zero_percentage = (
            year_df[year_df[column] == 0].shape[0]
            / year_df.shape[0]
            * 100
        )

        print(f"{column} - Year: % of 0s: {zero_percentage}")

    # create scatter with min and max values
    fig.add_trace(
        go.Scatter(
            x=station_df.index.year.unique(),
            y=min_values,
            mode="lines+markers",
            name=column + " Min Values",
        )
    )

    fig.add_trace(
        go.Scatter(
            x=station_df.index.year.unique(),
            y=max_values,
            mode="lines+markers",
            name=column + " Max Values",
        )
    )

    min_values = min_values[np.isfinite(min_values)]
    max_values = max_values[np.isfinite(max_values)]

    min_mean = np.mean(min_values)
    min_std = np.std(min_values)

    max_mean = np.mean(max_values)
    max_std = np.std(max_values)

    bacteria_info_df.loc[
        "Min Value", (105, column)
    ] = f"{min_mean:.2f} ± {min_std:.2f}"
    bacteria_info_df.loc[
        "Max Value", (105, column)
    ] = f"{max_mean:.2f} ± {max_std:.2f}"

fig.update_layout(
    title="Min and Max values for Station 105",
    xaxis_title="Year",
    yaxis_title="MPN/100ml",
    font=dict(
        size=18,
    ),
    legend=dict(yanchor="top", y=0.99, xanchor="right", x=0.99),
)

fig.write_html(
    os.path.join(
        data_folder,
        "plots",
        "min_max_surface_bacteria",
        f"station105.html",
    )
)

fig.show()

# Trend Analysis

In [65]:
diff_columns = np.array(["DateTime", "Station"])

## Surface

In [66]:
for station_id in surface_df["Station"].unique():
    station_df = surface_df[surface_df["Station"] == station_id].copy()

    for column in station_df.columns.difference(diff_columns):
        df = station_df[["DateTime", column]].copy()

        df.set_index("DateTime", inplace=True)

        df.dropna(inplace=True)

        date_range = df.index
        date_range = date_range.min(), date_range.max()

        # make sure that the dataframe starts and finishes in the same month
        start_index = df[df.index.month == date_range[1].month].index[0]

        # Slice the dataframe to start from the found index
        df = df.loc[start_index:]

        # ===== Prophet =====

        df.index.name = "ds"

        df = df.reset_index()

        df.rename(columns={column: "y"}, inplace=True)

        # using prophet

        model = Prophet()
        model.fit(df)
        # Make predictions for both columns
        future = model.make_future_dataframe(periods=0)
        forecast = model.predict(future)

        # Merging forecasted data with your original data
        forecasting_final = pd.merge(
            forecast,
            df,
            how="inner",
            on="ds",
        )

        # compute linear regression on trend
        X = np.arange(df.shape[0])
        X = sm.add_constant(X)
        y = df["y"].copy()

        model = sm.OLS(y, X)
        results = model.fit()

        # plot the line of the linear regression
        line = pd.Series(results.predict(X), index=df['ds'])

        fig = go.Figure()

        fig.add_trace(
            go.Scatter(
                x=df['ds'],
                y=df["y"],
                mode="lines",
                name="Original",
            )
        )

        fig.add_trace(
            go.Scatter(
                x=forecasting_final["ds"],
                y=forecasting_final["trend"],
                mode="lines",
                name="Trend",
            )
        )

        slope = results.params.iloc[1]
        print(f"{column} - Slope: {slope}")

        p_value = results.pvalues.iloc[1]
        print(f"{column} - P-value: {p_value}")

        fig.add_trace(
            go.Scatter(
                x=line.index,
                y=line,
                mode="lines",
                name=f"Linear Regression",
                line=dict(dash="dash", color="black"),
            ),
        )

        start_date = df['ds'].min()
        end_date = df['ds'].max()

        fig.update_layout(
            xaxis_title="Date",
            yaxis_title=column,
            font=dict(
                size=18,
            ),
            title=f"{station_id} - {column} - {start_date.strftime('%Y-%m-%d')} - {end_date.strftime('%Y-%m-%d')}",
        )

        fig.show()

18:26:27 - cmdstanpy - INFO - Chain [1] start processing
18:26:27 - cmdstanpy - INFO - Chain [1] done processing


Air Temperature (°C) - Slope: 0.010388430442687066
Air Temperature (°C) - P-value: 0.002433672823393708


18:26:27 - cmdstanpy - INFO - Chain [1] start processing
18:26:27 - cmdstanpy - INFO - Chain [1] done processing


Ammonium (mg/l) - Slope: -0.00011507691916459575
Ammonium (mg/l) - P-value: 7.813091778464309e-07


18:26:27 - cmdstanpy - INFO - Chain [1] start processing
18:26:27 - cmdstanpy - INFO - Chain [1] done processing


...

TOC (mg/l) - Slope: 0.001914693519884808
TOC (mg/l) - P-value: 0.010040681334182225


18:26:35 - cmdstanpy - INFO - Chain [1] start processing
18:26:35 - cmdstanpy - INFO - Chain [1] done processing


Water Temperature (°C) - Slope: -0.0015405125740060998
Water Temperature (°C) - P-value: 0.40976428295950085


18:26:36 - cmdstanpy - INFO - Chain [1] start processing
18:26:36 - cmdstanpy - INFO - Chain [1] done processing


pH - Slope: -0.00013586623682659488
pH - P-value: 0.062767359656555


## Ground

In [67]:
for station_id in ground_df["Station"].unique():
    station_df = ground_df[ground_df["Station"] == station_id].copy()

    for column in station_df.columns.difference(diff_columns):
        df = station_df[["DateTime", column]].copy()

        df.set_index("DateTime", inplace=True)

        df.dropna(inplace=True)
        
        if df.shape[0] == 0:
            continue

        date_range = df.index
        date_range = date_range.min(), date_range.max()

        # make sure that the dataframe starts and finishes in the same month
        start_index = df[df.index.month == date_range[1].month].index[0]

        # Slice the dataframe to start from the found index
        df = df.loc[start_index:]

        # ===== Prophet =====

        df.index.name = "ds"

        df = df.reset_index()

        df.rename(columns={column: "y"}, inplace=True)

        # using prophet

        model = Prophet()
        model.fit(df)
        # Make predictions for both columns
        future = model.make_future_dataframe(periods=0)
        forecast = model.predict(future)

        # Merging forecasted data with your original data
        forecasting_final = pd.merge(
            forecast,
            df,
            how="inner",
            on="ds",
        )

        # compute linear regression on trend
        X = np.arange(df.shape[0])
        X = sm.add_constant(X)
        y = df["y"].copy()

        model = sm.OLS(y, X)
        results = model.fit()

        # plot the line of the linear regression
        line = pd.Series(results.predict(X), index=df['ds'])

        fig = go.Figure()

        fig.add_trace(
            go.Scatter(
                x=df['ds'],
                y=df["y"],
                mode="lines",
                name="Original",
            )
        )

        fig.add_trace(
            go.Scatter(
                x=forecasting_final["ds"],
                y=forecasting_final["trend"],
                mode="lines",
                name="Trend",
            )
        )

        slope = results.params.iloc[1]
        print(f"{column} - Slope: {slope}")

        p_value = results.pvalues.iloc[1]
        print(f"{column} - P-value: {p_value}")

        fig.add_trace(
            go.Scatter(
                x=line.index,
                y=line,
                mode="lines",
                name=f"Linear Regression",
                line=dict(dash="dash", color="black"),
            ),
        )

        start_date = df['ds'].min()
        end_date = df['ds'].max()

        fig.update_layout(
            xaxis_title="Date",
            yaxis_title=column,
            font=dict(
                size=18,
            ),
            title=f"{station_id} - {column} - {start_date.strftime('%Y-%m-%d')} - {end_date.strftime('%Y-%m-%d')}",
        )

        fig.show()

18:26:36 - cmdstanpy - INFO - Chain [1] start processing
18:26:36 - cmdstanpy - INFO - Chain [1] done processing


Air Temperature (°C) - Slope: 0.01139780998844154
Air Temperature (°C) - P-value: 0.0024813687795161815


18:26:36 - cmdstanpy - INFO - Chain [1] start processing
18:26:36 - cmdstanpy - INFO - Chain [1] done processing


Ammonium (mg/l) - Slope: -4.776673662079784e-05
Ammonium (mg/l) - P-value: 0.5898559455432497


18:26:36 - cmdstanpy - INFO - Chain [1] start processing
18:26:36 - cmdstanpy - INFO - Chain [1] done processing


...

UVA254 (1/m) - Slope: 0.018862886856923153
UVA254 (1/m) - P-value: 3.204407814081926e-60


18:26:37 - cmdstanpy - INFO - Chain [1] start processing
18:26:38 - cmdstanpy - INFO - Chain [1] done processing


Water Temperature (°C) - Slope: 0.0010749329077905847
Water Temperature (°C) - P-value: 7.311863701559384e-23


18:26:38 - cmdstanpy - INFO - Chain [1] start processing
18:26:38 - cmdstanpy - INFO - Chain [1] done processing


pH - Slope: 0.0002045135311643432
pH - P-value: 0.016075265402993543


# Projections Comparison

## Flow River

In [68]:
column = 'Flow River Rate (m³/s)'

In [71]:
for station_id in surface_df["Station"].unique():
    station_df = surface_df[surface_df["Station"] == station_id].copy()

    df = station_df[["DateTime", column]].copy()
    
    df.dropna(inplace=True)
    
    projection_df = flow_river_projections[flow_river_projections["Station"] == station_id].copy()
    
    rcp45 = projection_df[projection_df["Type"] == "rcp45"]
    rcp85 = projection_df[projection_df["Type"] == "rcp85"]
    
    df.set_index("DateTime", inplace=True)
    
    rcp45.set_index("DateTime", inplace=True)
    rcp85.set_index("DateTime", inplace=True)
    
    # === Trend Computation ===
    
    # 1. Extract trend with Prophet
    
    # 1.1. Historical data
    
    df.index.name = "ds"

    df = df.reset_index()

    df.rename(columns={column: "y"}, inplace=True)

    model = Prophet()
    model.fit(df)
    # Make predictions for both columns
    future = model.make_future_dataframe(periods=0)
    forecast = model.predict(future)

    # Merging forecasted data with your original data
    hist_forecasting_final = pd.merge(
        forecast,
        df,
        how="inner",
        on="ds",
    )
    
    # 1.2. RCP 4.5
    
    rcp45.index.name = "ds"

    rcp45 = rcp45.reset_index()

    rcp45.rename(columns={column: "y"}, inplace=True)

    model = Prophet()
    model.fit(rcp45)
    # Make predictions for both columns
    future = model.make_future_dataframe(periods=0)
    forecast = model.predict(future)

    # Merging forecasted data with your original data
    rcp45_forecasting_final = pd.merge(
        forecast,
        rcp45,
        how="inner",
        on="ds",
    )
    
    # 1.3. RCP 8.5
    
    rcp85.index.name = "ds"

    rcp85 = rcp85.reset_index()

    rcp85.rename(columns={column: "y"}, inplace=True)

    model = Prophet()
    model.fit(rcp85)
    # Make predictions for both columns
    future = model.make_future_dataframe(periods=0)
    forecast = model.predict(future)

    # Merging forecasted data with your original data
    rcp85_forecasting_final = pd.merge(
        forecast,
        rcp85,
        how="inner",
        on="ds",
    )
    
    # 2. Compute linear regression on the trend
    
    # 2.1. Historical data
    
    X = np.arange(df.shape[0])
    X = sm.add_constant(X)
    y = df["y"].copy()

    model = sm.OLS(y, X)
    results = model.fit()

    # plot the line of the linear regression
    hist_line = pd.Series(results.predict(X), index=df['ds'])
    
    hist_slope = results.params.iloc[1]
    hist_p_value = results.pvalues.iloc[1]
    
    # 2.2. RCP 4.5
    
    X = np.arange(rcp45.shape[0])
    X = sm.add_constant(X)
    y = rcp45["y"].copy()

    model = sm.OLS(y, X)
    results = model.fit()

    # plot the line of the linear regression
    rcp45_line = pd.Series(results.predict(X), index=rcp45['ds'])
    
    rcp45_slope = results.params.iloc[1]
    rcp45_p_value = results.pvalues.iloc[1]
    
    # 2.3. RCP 8.5
    
    X = np.arange(rcp85.shape[0])
    X = sm.add_constant(X)
    y = rcp85["y"].copy()

    model = sm.OLS(y, X)
    results = model.fit()

    # plot the line of the linear regression
    rcp85_line = pd.Series(results.predict(X), index=rcp85['ds'])
    
    rcp85_slope = results.params.iloc[1]
    rcp85_p_value = results.pvalues.iloc[1]
    
    
    fig = go.Figure()
    
    fig.add_trace(
        go.Scatter(
            x=df['ds'],
            y=df['y'],
            mode="lines",
            name="Historical",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp45['ds'],
            y=rcp45['y'],
            mode="lines",
            name="RCP 4.5",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp85['ds'],
            y=rcp85['y'],
            mode="lines",
            name="RCP 8.5",
        )
    )
    
    
    fig.add_trace(
        go.Scatter(
            x=hist_forecasting_final["ds"],
            y=hist_forecasting_final["trend"],
            mode="lines",
            name="Historical Trend",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp45_forecasting_final["ds"],
            y=rcp45_forecasting_final["trend"],
            mode="lines",
            name="RCP 4.5 Trend",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp85_forecasting_final["ds"],
            y=rcp85_forecasting_final["trend"],
            mode="lines",
            name="RCP 8.5 Trend",
        )
    )
    
    # add box with regression slope and p-value for all the scenarios
    
    fig.add_annotation(
        x=0.95,
        y=0.99,
        xref="paper",
        yref="paper",
        text=f"Historical - Slope: {hist_slope:.3f}, P-value: {hist_p_value:.2f}",
        showarrow=False,
    )
    
    fig.add_annotation(
        x=0.95,
        y=0.93,
        xref="paper",
        yref="paper",
        text=f"RCP 4.5 - Slope: {rcp45_slope:.3f}, P-value: {rcp45_p_value:.2f}",
        showarrow=False,
    )
    
    fig.add_annotation(
        x=0.95,
        y=0.87,
        xref="paper",
        yref="paper",
        text=f"RCP 8.5 - Slope: {rcp85_slope:.3f}, P-value: {rcp85_p_value:.2f}",
        showarrow=False,
    )
    
    
    
    fig.update_layout(
        xaxis_title="Date",
        yaxis_title=column,
        font=dict(
            size=18,
        ),
        title=f"{station_id} - {column}",
    )
    
    fig.show()

18:27:53 - cmdstanpy - INFO - Chain [1] start processing
18:27:54 - cmdstanpy - INFO - Chain [1] done processing
18:27:54 - cmdstanpy - INFO - Chain [1] start processing
18:27:54 - cmdstanpy - INFO - Chain [1] done processing
18:27:54 - cmdstanpy - INFO - Chain [1] start processing
18:27:54 - cmdstanpy - INFO - Chain [1] done processing


18:27:54 - cmdstanpy - INFO - Chain [1] start processing
18:27:54 - cmdstanpy - INFO - Chain [1] done processing
18:27:54 - cmdstanpy - INFO - Chain [1] start processing
18:27:54 - cmdstanpy - INFO - Chain [1] done processing
18:27:55 - cmdstanpy - INFO - Chain [1] start processing
18:27:55 - cmdstanpy - INFO - Chain [1] done processing


18:27:55 - cmdstanpy - INFO - Chain [1] start processing
18:27:55 - cmdstanpy - INFO - Chain [1] done processing
18:27:55 - cmdstanpy - INFO - Chain [1] start processing
18:27:55 - cmdstanpy - INFO - Chain [1] done processing
18:27:55 - cmdstanpy - INFO - Chain [1] start processing
18:27:55 - cmdstanpy - INFO - Chain [1] done processing


## Air Temperature

In [46]:
column = 'Air Temperature (°C)'

In [55]:
for station_id in surface_df["Station"].unique():
    station_df = surface_df[surface_df["Station"] == station_id].copy()

    df = station_df[["DateTime", column]].copy()
    
    projection_df = air_temp_projections[air_temp_projections["Station"] == station_id].copy()
    
    rcp45 = projection_df[projection_df["Type"] == "rcp45"]
    rcp85 = projection_df[projection_df["Type"] == "rcp85"]
    
    df.set_index("DateTime", inplace=True)
    
    rcp45.set_index("DateTime", inplace=True)
    rcp85.set_index("DateTime", inplace=True)
    
    # === Trend Computation ===
    
    # 1. Extract trend with Prophet
    
    # 1.1. Historical data
    
    df.index.name = "ds"

    df = df.reset_index()

    df.rename(columns={column: "y"}, inplace=True)

    model = Prophet()
    model.fit(df)
    # Make predictions for both columns
    future = model.make_future_dataframe(periods=0)
    forecast = model.predict(future)

    # Merging forecasted data with your original data
    hist_forecasting_final = pd.merge(
        forecast,
        df,
        how="inner",
        on="ds",
    )
    
    # 1.2. RCP 4.5
    
    rcp45.index.name = "ds"

    rcp45 = rcp45.reset_index()

    rcp45.rename(columns={column: "y"}, inplace=True)

    model = Prophet()
    model.fit(rcp45)
    # Make predictions for both columns
    future = model.make_future_dataframe(periods=0)
    forecast = model.predict(future)

    # Merging forecasted data with your original data
    rcp45_forecasting_final = pd.merge(
        forecast,
        rcp45,
        how="inner",
        on="ds",
    )
    
    # 1.3. RCP 8.5
    
    rcp85.index.name = "ds"

    rcp85 = rcp85.reset_index()

    rcp85.rename(columns={column: "y"}, inplace=True)

    model = Prophet()
    model.fit(rcp85)
    # Make predictions for both columns
    future = model.make_future_dataframe(periods=0)
    forecast = model.predict(future)

    # Merging forecasted data with your original data
    rcp85_forecasting_final = pd.merge(
        forecast,
        rcp85,
        how="inner",
        on="ds",
    )
    
    # 2. Compute linear regression on the trend
    
    # 2.1. Historical data
    
    X = np.arange(df.shape[0])
    X = sm.add_constant(X)
    y = df["y"].copy()

    model = sm.OLS(y, X)
    results = model.fit()

    # plot the line of the linear regression
    hist_line = pd.Series(results.predict(X), index=df['ds'])
    
    hist_slope = results.params.iloc[1]
    hist_p_value = results.pvalues.iloc[1]
    
    # 2.2. RCP 4.5
    
    X = np.arange(rcp45.shape[0])
    X = sm.add_constant(X)
    y = rcp45["y"].copy()

    model = sm.OLS(y, X)
    results = model.fit()

    # plot the line of the linear regression
    rcp45_line = pd.Series(results.predict(X), index=rcp45['ds'])
    
    rcp45_slope = results.params.iloc[1]
    rcp45_p_value = results.pvalues.iloc[1]
    
    # 2.3. RCP 8.5
    
    X = np.arange(rcp85.shape[0])
    X = sm.add_constant(X)
    y = rcp85["y"].copy()

    model = sm.OLS(y, X)
    results = model.fit()

    # plot the line of the linear regression
    rcp85_line = pd.Series(results.predict(X), index=rcp85['ds'])
    
    rcp85_slope = results.params.iloc[1]
    rcp85_p_value = results.pvalues.iloc[1]
    
    
    fig = go.Figure()
    
    fig.add_trace(
        go.Scatter(
            x=df['ds'],
            y=df['y'],
            mode="lines",
            name="Historical",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp45['ds'],
            y=rcp45['y'],
            mode="lines",
            name="RCP 4.5",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp85['ds'],
            y=rcp85['y'],
            mode="lines",
            name="RCP 8.5",
        )
    )
    
    
    fig.add_trace(
        go.Scatter(
            x=hist_forecasting_final["ds"],
            y=hist_forecasting_final["trend"],
            mode="lines",
            name="Historical Trend",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp45_forecasting_final["ds"],
            y=rcp45_forecasting_final["trend"],
            mode="lines",
            name="RCP 4.5 Trend",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp85_forecasting_final["ds"],
            y=rcp85_forecasting_final["trend"],
            mode="lines",
            name="RCP 8.5 Trend",
        )
    )
    
    # add box with regression slope and p-value for all the scenarios
    
    fig.add_annotation(
        x=0.95,
        y=0.99,
        xref="paper",
        yref="paper",
        text=f"Historical - Slope: {hist_slope:.3f}, P-value: {hist_p_value:.2f}",
        showarrow=False,
    )
    
    fig.add_annotation(
        x=0.95,
        y=0.93,
        xref="paper",
        yref="paper",
        text=f"RCP 4.5 - Slope: {rcp45_slope:.3f}, P-value: {rcp45_p_value:.2f}",
        showarrow=False,
    )
    
    fig.add_annotation(
        x=0.95,
        y=0.87,
        xref="paper",
        yref="paper",
        text=f"RCP 8.5 - Slope: {rcp85_slope:.3f}, P-value: {rcp85_p_value:.2f}",
        showarrow=False,
    )
    
    
    
    fig.update_layout(
        xaxis_title="Date",
        yaxis_title=column,
        font=dict(
            size=18,
        ),
        title=f"{station_id} - {column}",
    )
    
    fig.show()

18:18:22 - cmdstanpy - INFO - Chain [1] start processing
18:18:22 - cmdstanpy - INFO - Chain [1] done processing
18:18:22 - cmdstanpy - INFO - Chain [1] start processing
18:18:22 - cmdstanpy - INFO - Chain [1] done processing
18:18:22 - cmdstanpy - INFO - Chain [1] start processing
18:18:22 - cmdstanpy - INFO - Chain [1] done processing


18:18:23 - cmdstanpy - INFO - Chain [1] start processing
18:18:23 - cmdstanpy - INFO - Chain [1] done processing
18:18:23 - cmdstanpy - INFO - Chain [1] start processing
18:18:23 - cmdstanpy - INFO - Chain [1] done processing
18:18:23 - cmdstanpy - INFO - Chain [1] start processing
18:18:23 - cmdstanpy - INFO - Chain [1] done processing


18:18:24 - cmdstanpy - INFO - Chain [1] start processing
18:18:24 - cmdstanpy - INFO - Chain [1] done processing
18:18:24 - cmdstanpy - INFO - Chain [1] start processing
18:18:24 - cmdstanpy - INFO - Chain [1] done processing
18:18:24 - cmdstanpy - INFO - Chain [1] start processing
18:18:24 - cmdstanpy - INFO - Chain [1] done processing


In [ ]:
# Se si fa dal 2000 in poi, si vede che la temperatura aumenta

# Precipitation

In [39]:
column = 'Cumulated Rainfall (mm)'

In [41]:
for station_id in surface_df["Station"].unique():
    station_df = surface_df[surface_df["Station"] == station_id].copy()

    df = station_df[["DateTime", column]].copy()
    
    projection_df = precip_projections[precip_projections["Station"] == station_id].copy()
    
    rcp45 = projection_df[projection_df["Type"] == "rcp45"]
    rcp85 = projection_df[projection_df["Type"] == "rcp85"]
    
    # === Trend Computation ===
    
    # 1. Extract trend with Prophet
    
    # 1.1. Historical data
    
    df.index.name = "ds"

    df = df.reset_index()

    df.rename(columns={column: "y"}, inplace=True)

    model = Prophet()
    model.fit(df)
    # Make predictions for both columns
    future = model.make_future_dataframe(periods=0)
    forecast = model.predict(future)

    # Merging forecasted data with your original data
    hist_forecasting_final = pd.merge(
        forecast,
        df,
        how="inner",
        on="ds",
    )
    
    # 1.2. RCP 4.5
    
    rcp45.index.name = "ds"

    rcp45 = rcp45.reset_index()

    rcp45.rename(columns={column: "y"}, inplace=True)

    model = Prophet()
    model.fit(rcp45)
    # Make predictions for both columns
    future = model.make_future_dataframe(periods=0)
    forecast = model.predict(future)

    # Merging forecasted data with your original data
    rcp45_forecasting_final = pd.merge(
        forecast,
        rcp45,
        how="inner",
        on="ds",
    )
    
    # 1.3. RCP 8.5
    
    rcp85.index.name = "ds"

    rcp85 = rcp85.reset_index()

    rcp85.rename(columns={column: "y"}, inplace=True)

    model = Prophet()
    model.fit(rcp85)
    # Make predictions for both columns
    future = model.make_future_dataframe(periods=0)
    forecast = model.predict(future)

    # Merging forecasted data with your original data
    rcp85_forecasting_final = pd.merge(
        forecast,
        rcp85,
        how="inner",
        on="ds",
    )
    
    # 2. Compute linear regression on the trend
    
    # 2.1. Historical data
    
    X = np.arange(df.shape[0])
    X = sm.add_constant(X)
    y = df["y"].copy()

    model = sm.OLS(y, X)
    results = model.fit()

    # plot the line of the linear regression
    hist_line = pd.Series(results.predict(X), index=df['ds'])
    
    hist_slope = results.params.iloc[1]
    hist_p_value = results.pvalues.iloc[1]
    
    # 2.2. RCP 4.5
    
    X = np.arange(rcp45.shape[0])
    X = sm.add_constant(X)
    y = rcp45["y"].copy()

    model = sm.OLS(y, X)
    results = model.fit()

    # plot the line of the linear regression
    rcp45_line = pd.Series(results.predict(X), index=rcp45['ds'])
    
    rcp45_slope = results.params.iloc[1]
    rcp45_p_value = results.pvalues.iloc[1]
    
    # 2.3. RCP 8.5
    
    X = np.arange(rcp85.shape[0])
    X = sm.add_constant(X)
    y = rcp85["y"].copy()

    model = sm.OLS(y, X)
    results = model.fit()

    # plot the line of the linear regression
    rcp85_line = pd.Series(results.predict(X), index=rcp85['ds'])
    
    rcp85_slope = results.params.iloc[1]
    rcp85_p_value = results.pvalues.iloc[1]
    
    
    fig = go.Figure()
    
    fig.add_trace(
        go.Scatter(
            x=df['DateTime'],
            y=df[column],
            mode="lines",
            name="Historical",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp45['DateTime'],
            y=rcp45[column],
            mode="lines",
            name="RCP 4.5",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp85['DateTime'],
            y=rcp85[column],
            mode="lines",
            name="RCP 8.5",
        )
    )
    
    
    fig.add_trace(
        go.Scatter(
            x=hist_forecasting_final["ds"],
            y=hist_forecasting_final["trend"],
            mode="lines",
            name="Historical Trend",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp45_forecasting_final["ds"],
            y=rcp45_forecasting_final["trend"],
            mode="lines",
            name="RCP 4.5 Trend",
        )
    )
    
    fig.add_trace(
        go.Scatter(
            x=rcp85_forecasting_final["ds"],
            y=rcp85_forecasting_final["trend"],
            mode="lines",
            name="RCP 8.5 Trend",
        )
    )
    
    # add box with regression slope and p-value for all the scenarios
    
    fig.add_annotation(
        x=0.05,
        y=0.95,
        xref="paper",
        yref="paper",
        text=f"Historical - Slope: {hist_slope:.2f}, P-value: {hist_p_value:.2f}",
        showarrow=False,
    )
    
    fig.add_annotation(
        x=0.05,
        y=0.90,
        xref="paper",
        yref="paper",
        text=f"RCP 4.5 - Slope: {rcp45_slope:.2f}, P-value: {rcp45_p_value:.2f}",
        showarrow=False,
    )
    
    fig.add_annotation(
        x=0.05,
        y=0.85,
        xref="paper",
        yref="paper",
        text=f"RCP 8.5 - Slope: {rcp85_slope:.2f}, P-value: {rcp85_p_value:.2f}",
        showarrow=False,
    )
    
    
    
    fig.update_layout(
        xaxis_title="Date",
        yaxis_title=column,
        font=dict(
            size=18,
        ),
        title=f"{station_id} - {column}",
    )
    
    fig.show()

/Users/massimilianoarca/Library/Caches/pypoetry/virtualenvs/climate-change-MEYtuKH4-py3.11/lib/python3.11/site-packages/prophet/forecaster.py:287: UserWarning:

Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.



DateParseError: day is out of range for month: 0, at position 0